# n-Photon Compton Scattering Process

In this file, we set up an n-photon Compton scattering process. A Compton scattering
process looks like $k^n e^- \to k e^-$.

You can download this file as a [jupyter notebook](compton.ipynb).

In [1]:
using QEDFeynmanDiagrams

We need QEDcore of the [QEDjl-project](https://github.com/QEDjl-project) for base
functionality and a process type, for which we can use the `Mocks` submodule
from QEDbase for this tutorial. Downstream, a `ScatteringProcess` from QEDprocesses.jl
could be used, for example.

In [2]:
using QEDcore
using QEDbase.Mocks

Let's decide how many photons our electron interacts with:

In [3]:
n = 4;

Now we setup the scattering process accordingly. We consider all spin/polarization
combinations of the particles except for the incoming photons, where the polarizations are synced using `QEDbase.SyncedPolarization`.
This emulates all synced photons having the same, but still indefinite, polarization, for example from a laser.
> **Note**
>
> Currently, this process uses outgoing photons instead of incoming photons, because there is not yet a
> `PhaseSpaceLayout` for more than two incoming particles in QEDcore.jl. See issue https://github.com/QEDjl-project/QEDcore.jl/issues/103

In [4]:
proc = QEDbase.Mocks.MockProcessSP(
    (Electron(), Photon()),                        # incoming particles
    (Electron(), ntuple(_ -> Photon(), n)...),     # outgoing particles
    (AllSpin(), AllPol()),                         # incoming particle spin/pols
    (AllSpin(), ntuple(_ -> SyncedPol(1), n)...),  # outgoing particle spin/pols
)

QEDbase.Mocks.MockProcessSP{Tuple{Electron, Photon}, Tuple{Electron, Vararg{Photon, 4}}, Tuple{AllSpin, AllPolarization}, Tuple{AllSpin, Vararg{SyncedPolarization{1}, 4}}}((electron, photon), (electron, photon, photon, photon, photon), (all spins, all polarizations), (all spins, synced polarization 1, synced polarization 1, synced polarization 1, synced polarization 1))

The `number_of_diagrams` function returns how many diagrams there are for a given process.
For an n-photon Compton process with `n` incoming photons, this should be $(n+1)!$.

In [5]:
number_of_diagrams(proc)

120

Next, we can generate the DAG representing the computation for our scattering process'
squared matrix element. This uses [`ComputableDAGs.jl`](https://github.com/ComputableDAGs/ComputableDAGs.jl).

In [6]:
dag = graph(proc)

Graph:
  Nodes: Total: 2262, QEDFeynmanDiagrams.ComputeTask_SpinPolCumulation: 1, QEDFeynmanDiagrams.ComputeTask_BaseState: 14, 
         QEDFeynmanDiagrams.ComputeTask_Pair: 264, QEDFeynmanDiagrams.ComputeTask_PropagatePairs: 152, QEDFeynmanDiagrams.ComputeTask_CollectTriples: 16, 
         QEDFeynmanDiagrams.ComputeTask_CollectPairs: 152, DataTask: 1153, QEDFeynmanDiagrams.ComputeTask_Propagator: 30, 
         QEDFeynmanDiagrams.ComputeTask_TripleNegated: 480
  Edges: 4185
  Total Compute Effort: 0.0
  Total Data Transfer: 0.0
  Total Compute Intensity: 0.0


In this graph output you can see the number of nodes necessary to compute.
Note that for larger processes, the number of total nodes can be *lower* than
the number of Feynman diagrams, even with the added complexity of considering
multiple spin and polarization combinations. This is the result of efficient
reuse of reappearing parts of Feynman diagrams.

To continue, we will need [`ComputableDAGs.jl`](https://github.com/ComputableDAGs/ComputableDAGs.jl). Since `ComputableDAGs.jl` uses
`RuntimeGeneratedFunction`s as the return type of `ComputableDAGs.get_compute_function`, we need
to initialize it in our current module.

In [7]:
using ComputableDAGs
using RuntimeGeneratedFunctions
RuntimeGeneratedFunctions.init(@__MODULE__)

Now we need an input for the function, which is a `QEDcore.PhaseSpacePoint`.
For now, we generate random momenta for every particle. In the future, QEDevents
will be able to generate physical `PhaseSpacePoint`s.

In [8]:
psp = PhaseSpacePoint(
    proc,
    MockModel(),
    FlatPhaseSpaceLayout(TwoBodyRestSystem()),
    tuple((rand(SFourMomentum) for _ in 1:number_incoming_particles(proc))...),
    tuple((rand(SFourMomentum) for _ in 1:number_outgoing_particles(proc))...),
)

PhaseSpacePoint:
    process: QEDbase.Mocks.MockProcessSP{Tuple{Electron, Photon}, Tuple{Electron, Vararg{Photon, 4}}, Tuple{AllSpin, AllPolarization}, Tuple{AllSpin, Vararg{SyncedPolarization{1}, 4}}}((electron, photon), (electron, photon, photon, photon, photon), (all spins, all polarizations), (all spins, synced polarization 1, synced polarization 1, synced polarization 1, synced polarization 1))
    model: mock model
    phase space layout: FlatPhaseSpaceLayout{TwoBodyTargetSystem{Energy{2}}}(TwoBodyTargetSystem{Energy{2}}(Energy{2}()))
    incoming particles:
     -> incoming electron: [0.19307304186829854, 0.626842057632204, 0.2699623475272559, 0.11713597513888407]
     -> incoming photon: [0.07465487700003803, 0.2285822745288122, 0.16424184663147456, 0.17814508924620276]
    outgoing particles:
     -> outgoing electron: [0.7433679662936301, 0.3874618121312521, 0.33699988146906223, 0.008817836388133271]
     -> outgoing photon: [0.8086480021446535, 0.8268049633708832, 0.35258026

With the DAG, the process, `RuntimeGeneratedFunctions` initialized, and an input type to use,
we can now generate the actual computable function:

In [9]:
func = get_compute_function(
    dag, proc, cpu_st(), @__MODULE__; concrete_input_type = typeof(psp)
);

Finally, we can test that the function actually runs and computes something by
simply calling it on the `PhaseSpacePoint`:

In [10]:
func(psp)

0.21500205317158202

We can benchmark the execution speed too:

In [11]:
using BenchmarkTools
@benchmark func($psp)

BenchmarkTools.Trial: 10000 samples with 1 evaluation per sample.
 Range (min … max):  34.364 μs … 86.432 μs  ┊ GC (min … max): 0.00% … 0.00%
 Time  (median):     34.775 μs              ┊ GC (median):    0.00%
 Time  (mean ± σ):   35.285 μs ±  2.426 μs  ┊ GC (mean ± σ):  0.00% ± 0.00%

  ▄██▅ ▁                                             ▂▁       ▂
  ███████▅▁▃▁▁▁▃▁▅▇▆▆▄▁▁▁▅▁▃▁▁▄▃▃▄▃▁▃▃▄▄▁▃▄▃▃▄▃▁▄▄▄▆████▆▅▆▆▅ █
  34.4 μs      Histogram: log(frequency) by time      46.1 μs <

 Memory estimate: 256 bytes, allocs estimate: 2.

---

*This notebook was generated using [Literate.jl](https://github.com/fredrikekre/Literate.jl).*